In [13]:
%matplotlib inline
import openmc

In [15]:
uo2 = openmc.Material(1, "uo2")


In [17]:
mat = openmc.Material()

In [19]:
# Add nuclides to uo2
uo2.add_nuclide('U235', 0.03)
uo2.add_nuclide('U238', 0.97)
uo2.add_nuclide('O16', 2.0)

In [20]:
uo2.set_density('g/cm3', 10.0)

In [21]:
zirconium = openmc.Material(name="zirconium")
zirconium.add_element('Zr', 1.0)
zirconium.set_density('g/cm3', 6.6)

water = openmc.Material(name="h2o")
water.add_nuclide('H1', 2.0)
water.add_nuclide('O16', 1.0)
water.set_density('g/cm3', 1.0)

In [22]:
water.add_s_alpha_beta('c_H_in_H2O')

In [23]:
materials = openmc.Materials([uo2, zirconium, water])

In [24]:
materials = openmc.Materials()
materials.append(uo2)
materials += [zirconium, water]
isinstance(materials, list)

True

In [25]:
materials.export_to_xml()
!cat materials.xml

<?xml version='1.0' encoding='utf-8'?>
<materials>
  <material depletable="true" id="1" name="uo2">
    <density units="g/cm3" value="10.0"/>
    <nuclide ao="0.03" name="U235"/>
    <nuclide ao="0.97" name="U238"/>
    <nuclide ao="2.0" name="O16"/>
  </material>
  <material id="5" name="zirconium">
    <density units="g/cm3" value="6.6"/>
    <nuclide ao="0.5145" name="Zr90"/>
    <nuclide ao="0.1122" name="Zr91"/>
    <nuclide ao="0.1715" name="Zr92"/>
    <nuclide ao="0.1738" name="Zr94"/>
    <nuclide ao="0.028" name="Zr96"/>
  </material>
  <material id="6" name="h2o">
    <density units="g/cm3" value="1.0"/>
    <nuclide ao="2.0" name="H1"/>
    <nuclide ao="1.0" name="O16"/>
    <sab name="c_H_in_H2O"/>
  </material>
</materials>


In [26]:
water.remove_nuclide('O16')
water.add_element('O', 1.0)

materials.export_to_xml()
!cat materials.xml

<?xml version='1.0' encoding='utf-8'?>
<materials>
  <material depletable="true" id="1" name="uo2">
    <density units="g/cm3" value="10.0"/>
    <nuclide ao="0.03" name="U235"/>
    <nuclide ao="0.97" name="U238"/>
    <nuclide ao="2.0" name="O16"/>
  </material>
  <material id="5" name="zirconium">
    <density units="g/cm3" value="6.6"/>
    <nuclide ao="0.5145" name="Zr90"/>
    <nuclide ao="0.1122" name="Zr91"/>
    <nuclide ao="0.1715" name="Zr92"/>
    <nuclide ao="0.1738" name="Zr94"/>
    <nuclide ao="0.028" name="Zr96"/>
  </material>
  <material id="6" name="h2o">
    <density units="g/cm3" value="1.0"/>
    <nuclide ao="2.0" name="H1"/>
    <nuclide ao="0.9976206" name="O16"/>
    <nuclide ao="0.000379" name="O17"/>
    <nuclide ao="0.0020004" name="O18"/>
    <sab name="c_H_in_H2O"/>
  </material>
</materials>


In [29]:
# Create PuO2 material
puo2 = openmc.Material()
puo2.add_nuclide('Pu239', 0.94)
puo2.add_nuclide('Pu240', 0.06)
puo2.add_nuclide('O16', 2.0)
puo2.set_density('g/cm3', 11.5)

# Create the mixture
mox = openmc.Material.mix_materials([uo2, puo2], [0.97, 0.03], 'wo')

In [30]:
sphere = openmc.Sphere(r=1.0)

In [31]:
inside_sphere = -sphere
outside_sphere = +sphere

In [32]:
print((0,0,0) in inside_sphere, (0,0,2) in inside_sphere)
print((0,0,0) in outside_sphere, (0,0,2) in outside_sphere)

True False
False True


In [33]:
z_plane = openmc.ZPlane(z0=0)
northern_hemisphere = -sphere & +z_plane

In [34]:
northern_hemisphere.bounding_box

BoundingBox(lower_left=(-1.0, -1.0, 0.0), upper_right=(1.0, 1.0, 1.0))

In [35]:
cell = openmc.Cell()
cell.region = northern_hemisphere

In [36]:
cell.fill = water

In [37]:
universe = openmc.Universe()
universe.add_cell(cell)

# this also works
universe = openmc.Universe(cells=[cell])

In [43]:
materials.cross_sections = '/mnt/d/openmc/endfb80_hdf5/cross_sections.xml'

In [45]:
universe.plot(width=(2.0, 2.0))

RuntimeError: No cross_sections.xml file was specified in materials.xml or in the OPENMC_CROSS_SECTIONS environment variable. OpenMC needs such a file to identify where to find data libraries. Please consult the user's guide at https://docs.openmc.org/ for information on how to set up data libraries.